In [1]:
!pip install -qU langchain_openai langchain_huggingface langchain_core langchain langchain_community langchain-text-splitters unstructured


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 18.1 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.3/55.3 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 414.1/414.1 kB 24.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 61.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 69.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 57.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 590.6/590.6 kB 33.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 167.6/167.6 kB 15.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 77.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 113.6/113.6 kB 9.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.9/50.9 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 300.7/300.7 kB 21.7 MB/s eta 0:00:00
   ━━━━━

In [2]:
!pip install -qU faiss-cpu python-pptx==1.0.2 nltk==3.9.1 pymupdf beautifulsoup4 lxml


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.8/472.8 kB 14.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.7/30.7 MB 14.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 20.0/20.0 MB 27.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 165.1/165.1 kB 14.2 MB/s eta 0:00:00


In [3]:
import os
import getpass

os.environ["OPENAI_API_KEY"] = getpass.getpass("Enter Your OpenAI API Key: ")

Enter Your OpenAI API Key: ··········


In [4]:
import nest_asyncio

nest_asyncio.apply()

In [34]:
from langchain_community.document_loaders import DirectoryLoader
from langchain_community.document_loaders import UnstructuredMarkdownLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter

CHUNK_SIZE = 1000
CHUNK_OVERLAP = CHUNK_SIZE // 2

path = "sample_data"
text_loader = DirectoryLoader(path, glob="*.txt", loader_cls=UnstructuredMarkdownLoader)

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = CHUNK_SIZE,
    chunk_overlap  = CHUNK_OVERLAP,
    length_function = len
)

training_documents = text_splitter.split_documents(text_loader.load())

In [35]:
print(len(training_documents))

106


In [36]:
import uuid

id_set = set()

for document in training_documents:
  id = str(uuid.uuid4())
  while id in id_set:
    id = uuid.uuid4()
  id_set.add(id)
  document.metadata["id"] = id

In [46]:
TRAINING_DOC_LENGTH = len(training_documents)
BREAK1 = TRAINING_DOC_LENGTH - 24
BREAK2 = TRAINING_DOC_LENGTH - 12

training_split_documents = training_documents[:TRAINING_DOC_LENGTH - 24]
val_split_documents = training_documents[BREAK1:BREAK2]
test_split_documents = training_documents[BREAK2:]

In [47]:
print(len(training_split_documents))
print(len(val_split_documents))
print(len(test_split_documents))

82
12
12


In [48]:
from langchain_openai import ChatOpenAI
from langchain_core.prompts import ChatPromptTemplate

qa_chat_model = ChatOpenAI(
    model="gpt-4o-mini",
    temperature=0
)

qa_prompt = """\
Given the following context, you must generate questions based on only the provided context.

You are to generate {n_questions} questions which should be provided in the following format:

1. QUESTION #1
2. QUESTION #2
...

Context:
{context}
"""

qa_prompt_template = ChatPromptTemplate.from_template(qa_prompt)

question_generation_chain = qa_prompt_template | qa_chat_model

In [49]:
import tqdm
import uuid

async def create_questions(documents, n_questions):
    questions = {}
    relevant_docs = {}

    for document in tqdm.tqdm(documents):
        context = document.page_content

        # get questions by invoking the question generation chain
        response = await question_generation_chain.ainvoke(
            {"context": context, "n_questions": n_questions}
        )

        # split the response into two questions
        [question1, question2] = response.content.split("\n")

        # generate a unique id for the first question
        id1 = str(uuid.uuid4())
        while id1 in questions:
            id1 = str(uuid.uuid4())
        # store the first question
        questions[id1] = question1[2:].strip()

        # generate a unique id for the second question
        id2 = str(uuid.uuid4())
        while id2 in questions:
            id2 = str(uuid.uuid4())
        # store the second question
        questions[id2] = question2[2:].strip()

        # Store the relevant doc for each questions
        relevant_docs[id1] = [document.metadata["id"]]
        relevant_docs[id2] = [document.metadata["id"]]

    return questions, relevant_docs

In [50]:
training_questions, training_relevant_contexts = await create_questions(training_split_documents, 2)

100%|██████████| 82/82 [01:31<00:00,  1.12s/it]


In [51]:
print(training_questions, training_relevant_contexts)

{'de4d625a-2699-4108-955c-98bf64727d99': 'What is the purpose of templates in Shopify Flow?', '55d6816b-df29-428d-8a78-e74f74a61262': 'How can merchants utilize the template library in Shopify Flow?', 'def87f12-ed5d-49f9-86e2-24be1f1af812': 'What is required for the test web server to successfully send information to Shopify Flow?', '39ae4924-5863-4abc-bcd2-56a8d8af9f2c': 'What naming guidelines should be followed when creating a Flow trigger extension?', '6c3941aa-cf3d-49fb-9944-313f84acb849': 'What format should be used for naming a Flow action in Shopify?', 'd355b6c8-0da1-4048-b76d-49facf540bb9': 'What command is used to generate a new extension using Shopify CLI?', '3a1b68a7-1b5c-43ab-8c6b-c2515dcf0ee0': 'What command should you run to generate a new extension in your app directory using Shopify CLI?', 'a3ffe9c3-8873-4c39-b439-585f817e94d7': 'Where can you find the file representation of your generated extension after following the prompts?', '4ccd464a-1cdf-4931-b077-e28baa27665e':

In [42]:
val_questions, val_relevant_contexts = await create_questions(val_split_documents, 2)

100%|██████████| 12/12 [00:21<00:00,  1.81s/it]


In [52]:
print(val_questions, val_relevant_contexts)

{'d3ce989e-1b7a-4485-9662-649615cfda52': 'What actions are defined for the buttons in the provided function?', 'afe55661-f1d9-40db-b7eb-2fb30737e59d': 'What additional steps are required to configure a custom action in Shopify Flow?', 'addab304-12a6-4984-916a-2298edc02576': 'What is the purpose of the handle property in the context of importing Flow extensions into Shopify CLI?', '754ecd00-b9ab-45e1-8f38-ed7f608f8142': 'What are the requirements for creating a Partner account and using Shopify CLI v3.70.0 or higher?', '9fe5ad96-2951-48db-b298-b225179f74c7': "What happens to the handle property of extensions in your app's codebase after running the dev or deploy commands?", 'a3c5ea67-5e44-49cf-85f6-ea4216dac9bf': 'What is the purpose of the import command in relation to Partner Dashboard extensions?', 'ff0f101d-5026-415b-a763-ef68ddfa60ce': 'What command is used to import a Flow extension into your application?', 'dd95bb0f-47e6-4b58-bba5-d83eb2754ede': 'Where can you find the generated 

In [54]:
test_questions, test_relevant_contexts = await create_questions(test_split_documents, 2)

100%|██████████| 12/12 [00:14<00:00,  1.19s/it]


In [55]:
print(test_questions, test_relevant_contexts)

{'a5d7c3ac-3655-44bf-b5d4-12c95bb31aa3': "How can a schema file be referenced in an action extension's TOML?", '4bf731c3-2f5c-471a-b623-fd68e2c6edb8': "What property values need to be set to reference the return type schema in a trigger extension's TOML?", 'f78de3d5-8643-4e05-bdb1-8383b90982f5': "How can a schema file be referenced in the trigger extension's TOML?", '681635d9-6895-4fff-9900-13b0f21a3f62': 'What must the return_value object in the JSON response match in order to respond to an action request from Flow?', '70ba5530-3239-4d2e-a586-4d8343c90301': 'What is the status of the auction identified as "auction1"?', 'bbe12077-2a17-409a-82c0-081dd986d2c1': 'How many bids were placed in the auction named "My first auction"?', '328c14d9-7224-49ad-8f01-60ec833cffb3': 'What happens if a workflow uses a non-nullable field that is missing from the payload?', 'a199c858-27b2-409c-8f3e-62e0b0208864': 'What is the maximum response size allowed for an action before it results in a transient fa

In [56]:
import json

training_corpus = {train_item.metadata["id"] : train_item.page_content for train_item in training_split_documents}
train_dataset = {
    "questions" : training_questions,
    "relevant_contexts" : training_relevant_contexts,
    "corpus" : training_corpus
}
with open("training_dataset.jsonl", "w") as f:
  json.dump(train_dataset, f)

#####

val_corpus = {val_item.metadata["id"] : val_item.page_content for val_item in val_split_documents}
val_dataset = {
    "questions" : val_questions,
    "relevant_contexts" : val_relevant_contexts,
    "corpus" : val_corpus
}
with open("val_dataset.jsonl", "w") as f:
  json.dump(val_dataset, f)

#####

train_corpus = {test_item.metadata["id"] : test_item.page_content for test_item in test_split_documents}
test_dataset = {
    "questions" : test_questions,
    "relevant_contexts" : test_relevant_contexts,
    "corpus" : train_corpus
}
with open("test_dataset.jsonl", "w") as f:
  json.dump(test_dataset, f)

## Fine-tuning snowflake-arctic-embed-l

In [15]:
!pip install -qU sentence_transformers datasets pyarrow==15.0.2

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 38.3/38.3 MB 25.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.4/485.4 kB 36.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 12.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 17.5 MB/s eta 0:00:00


In [16]:
from sentence_transformers import SentenceTransformer

model_id = "Snowflake/snowflake-arctic-embed-l"
model = SentenceTransformer(model_id)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/252 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/85.4k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/107 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

1_Pooling%2Fconfig.json:   0%|          | 0.00/297 [00:00<?, ?B/s]

In [57]:
from torch.utils.data import DataLoader
from torch.utils.data import Dataset
from sentence_transformers import InputExample

BATCH_SIZE = 10

corpus = train_dataset['corpus']
queries = train_dataset['questions']
relevant_docs = train_dataset['relevant_contexts']

examples = []
for query_id, query in queries.items():
    doc_id = relevant_docs[query_id][0]
    text = corpus[doc_id]
    example = InputExample(texts=[query, text])
    examples.append(example)

loader = DataLoader(
    examples, batch_size=BATCH_SIZE
)

In [58]:
print(train_dataset)

{'questions': {'de4d625a-2699-4108-955c-98bf64727d99': 'What is the purpose of templates in Shopify Flow?', '55d6816b-df29-428d-8a78-e74f74a61262': 'How can merchants utilize the template library in Shopify Flow?', 'def87f12-ed5d-49f9-86e2-24be1f1af812': 'What is required for the test web server to successfully send information to Shopify Flow?', '39ae4924-5863-4abc-bcd2-56a8d8af9f2c': 'What naming guidelines should be followed when creating a Flow trigger extension?', '6c3941aa-cf3d-49fb-9944-313f84acb849': 'What format should be used for naming a Flow action in Shopify?', 'd355b6c8-0da1-4048-b76d-49facf540bb9': 'What command is used to generate a new extension using Shopify CLI?', '3a1b68a7-1b5c-43ab-8c6b-c2515dcf0ee0': 'What command should you run to generate a new extension in your app directory using Shopify CLI?', 'a3ffe9c3-8873-4c39-b439-585f817e94d7': 'Where can you find the file representation of your generated extension after following the prompts?', '4ccd464a-1cdf-4931-b077-

In [59]:
from sentence_transformers.losses import MatryoshkaLoss, MultipleNegativesRankingLoss

matryoshka_dimensions = [768, 512, 256, 128, 64]
inner_train_loss = MultipleNegativesRankingLoss(model)
train_loss = MatryoshkaLoss(
    model, inner_train_loss, matryoshka_dims=matryoshka_dimensions
)

In [60]:
from sentence_transformers.evaluation import InformationRetrievalEvaluator

corpus = val_dataset['corpus']
queries = val_dataset['questions']
relevant_docs = val_dataset['relevant_contexts']

evaluator = InformationRetrievalEvaluator(queries, corpus, relevant_docs)

In [61]:
import wandb
wandb.init(mode="disabled")

In [62]:
EPOCHS = 10
warmup_steps = int(len(loader) * EPOCHS * 0.1)

model.fit(
    train_objectives=[(loader, train_loss)],
    epochs=EPOCHS,
    warmup_steps=warmup_steps,
    output_path='AIE5-MidTerm-finetuned-embeddings',
    show_progress_bar=True,
    evaluator=evaluator,
    evaluation_steps=50
)

Computing widget examples:   0%|          | 0/1 [00:00<?, ?example/s]

In [64]:
from huggingface_hub import notebook_login

notebook_login()
hf_username = "thomfoolery"
model.push_to_hub(f"{hf_username}/AIE5-MidTerm-finetuned-embeddings")

model.safetensors:   0%|          | 0.00/1.34G [00:00<?, ?B/s]

'https://huggingface.co/thomfoolery/AIE5-MidTerm-finetuned-embeddings/commit/f7ca656c62a36c10efd3de835d9f529496a91c9b'